# WorldPop by Year Visualization

Properly visualize WorldPop data for individual years with country filtering.

In [1]:
import ee
import folium
import ipywidgets as widgets
from IPython.display import display

# Initialize GEE
ee.Initialize(project='tl-cities')
print('✅ GEE initialized successfully!')

✅ GEE initialized successfully!


## Helper Functions

In [2]:
def add_ee_layer(self, ee_image_object, vis_params, name):
    """Adds a method for displaying Earth Engine image tiles to folium map."""
    map_id_dict = ee.Image(ee_image_object).getMapId(vis_params)
    folium.raster_layers.TileLayer(
        tiles=map_id_dict['tile_fetcher'].url_format,
        attr='Map Data &copy; <a href="https://earthengine.google.com/">Google Earth Engine</a>',
        name=name,
        overlay=True,
        control=True
    ).add_to(self)

# Add the Earth Engine layer method to folium
folium.Map.add_ee_layer = add_ee_layer

def get_country_bounds(country_name):
    """Get country boundaries from GEE Large Scale International Boundary dataset"""
    countries = ee.FeatureCollection('USDOS/LSIB_SIMPLE/2017')
    country = countries.filter(ee.Filter.eq('country_na', country_name))
    return country

def get_country_center(country_geometry):
    """Get center coordinates of a country"""
    centroid = country_geometry.geometry().centroid()
    coords = centroid.coordinates().getInfo()
    return [coords[1], coords[0]]  # [lat, lon] for folium

## Explore WorldPop Data Structure

In [3]:
# Load WorldPop collection
dataset = ee.ImageCollection('WorldPop/GP/100m/pop_age_sex')

print("📊 WorldPop Dataset Information:")
print(f"Total images: {dataset.size().getInfo()}")

# Get available years
years = dataset.aggregate_array('year').distinct().sort().getInfo()
print(f"Available years: {years}")

# Get available countries 
countries_wp = dataset.aggregate_array('country').distinct().sort().getInfo()
print(f"Number of countries: {len(countries_wp)}")
print(f"First 10 countries: {countries_wp[:10]}")

# Check the first image
first_image = dataset.first()
bands = first_image.bandNames().getInfo()
print(f"Available bands: {bands}")

# Get properties of first image
props = first_image.getInfo()['properties']
print(f"\nSample image properties:")
for key in ['year', 'country', 'UNadj']:
    if key in props:
        print(f"  {key}: {props[key]}")

📊 WorldPop Dataset Information:
Total images: 243
Available years: [2020]
Number of countries: 243
First 10 countries: ['ABW', 'AFG', 'AGO', 'AIA', 'ALA', 'ALB', 'AND', 'ARE', 'ARG', 'ARM']
Available bands: ['population', 'M_0', 'M_1', 'M_5', 'M_10', 'M_15', 'M_20', 'M_25', 'M_30', 'M_35', 'M_40', 'M_45', 'M_50', 'M_55', 'M_60', 'M_65', 'M_70', 'M_75', 'M_80', 'F_0', 'F_1', 'F_5', 'F_10', 'F_15', 'F_20', 'F_25', 'F_30', 'F_35', 'F_40', 'F_45', 'F_50', 'F_55', 'F_60', 'F_65', 'F_70', 'F_75', 'F_80']

Sample image properties:
  year: 2020
  country: ABW


## Filter by Year - The Correct Way

In [4]:
# Test filtering by specific year
test_year = 2020
test_country = 'GBR'  # UK country code

print(f"🔍 Testing filter for year {test_year}")

# Filter by year
year_filtered = dataset.filter(ee.Filter.eq('year', test_year))
print(f"Images for {test_year}: {year_filtered.size().getInfo()}")

# Filter by year and country
year_country_filtered = dataset.filter(ee.Filter.eq('year', test_year)).filter(ee.Filter.eq('country', test_country))
print(f"Images for {test_year} in {test_country}: {year_country_filtered.size().getInfo()}")

# Get the first image for this year/country
if year_country_filtered.size().getInfo() > 0:
    test_image = year_country_filtered.first()
    test_props = test_image.getInfo()['properties']
    print(f"Found image: Year {test_props.get('year')}, Country {test_props.get('country')}")
else:
    print("No images found for this filter")
    # Try without country filter
    test_image = year_filtered.first()
    print("Using first image from year filter")

🔍 Testing filter for year 2020
Images for 2020: 243
Images for 2020 in GBR: 1
Found image: Year 2020, Country GBR


## Create Proper Year-Based Visualization

In [5]:
def get_worldpop_for_year(year):
    """Get WorldPop data for a specific year - the correct way"""
    
    # Filter collection by year
    year_collection = dataset.filter(ee.Filter.eq('year', year))
    
    # Create mosaic of all countries for that year
    year_mosaic = year_collection.mosaic()
    
    print(f"✅ Created mosaic for year {year} from {year_collection.size().getInfo()} images")
    
    return year_mosaic

# Test with 2020 data
pop_2020 = get_worldpop_for_year(2020)

# Visualization parameters
visualization = {
    'bands': ['population'],
    'min': 0.0,
    'max': 50.0,
    'palette': ['24126c', '1fff4f', 'd4ff50']
}

# Create global map for 2020
m_2020 = folium.Map(location=[34.769, 113.643], zoom_start=4)
m_2020.add_ee_layer(pop_2020, visualization, 'WorldPop 2020')

# Add colorbar
colormap = folium.LinearColormap(
    colors=['#24126c', '#1fff4f', '#d4ff50'],
    vmin=0, vmax=50,
    caption='Population 2020 (people per pixel)'
)
colormap.add_to(m_2020)

folium.LayerControl().add_to(m_2020)

print("🌍 Global WorldPop 2020 map:")
m_2020

✅ Created mosaic for year 2020 from 243 images
🌍 Global WorldPop 2020 map:


## Interactive Year and Country Selection

In [6]:
# Get country list from boundaries dataset (more complete)
countries = ee.FeatureCollection('USDOS/LSIB_SIMPLE/2017')
country_list = countries.aggregate_array('country_na').distinct().sort().getInfo()

# Create widgets
year_dropdown = widgets.Dropdown(
    options=years,
    value=2020,
    description='Year:',
    style={'description_width': 'initial'}
)

country_dropdown = widgets.Dropdown(
    options=country_list,
    value='United Kingdom',
    description='Country:',
    style={'description_width': 'initial'}
)

population_band = widgets.Dropdown(
    options=[
        ('Total Population', 'population'),
        ('Men Total', 'men'),
        ('Women Total', 'women'),
        ('Men 0-1 years', 'men_0'),
        ('Women 0-1 years', 'women_0'),
        ('Men 15-49 years', 'men_15_49'),
        ('Women 15-49 years', 'women_15_49')
    ],
    value='population',
    description='Population:',
    style={'description_width': 'initial'}
)

display(widgets.HBox([year_dropdown, country_dropdown]))
display(population_band)

Dropdown(description='Population:', options=(('Total Population', 'population'), ('Men Total', 'men'), ('Women…

## Country-Focused Map Function

In [7]:
def create_country_year_map(country_name, year, band):
    """Create a country-focused map for specific year and population band"""
    
    print(f"🗺️ Creating map: {country_name}, {year}, {band}")
    
    # Get country boundary
    country = get_country_bounds(country_name)
    country_geometry = country.first()
    
    # Get country center
    try:
        center_coords = get_country_center(country_geometry)
    except:
        center_coords = [0, 0]
    
    # Get WorldPop data for the year
    worldpop_year = get_worldpop_for_year(year)
    
    # Select the specific band
    pop_band = worldpop_year.select(band)
    
    # Clip to country (optional - you can comment this out to see surrounding areas)
    # pop_clipped = pop_band.clip(country_geometry.geometry())
    
    # Create map
    m = folium.Map(location=center_coords, zoom_start=6)
    
    # Visualization parameters
    vis_params = {
        'bands': [band],
        'min': 0.0,
        'max': 50.0,
        'palette': ['24126c', '1fff4f', 'd4ff50']
    }
    
    # Add population layer (use pop_clipped if you want country-only)
    layer_name = f'{band.title()} {year} - {country_name}'
    m.add_ee_layer(pop_band, vis_params, layer_name)
    
    # Add country boundary
    try:
        country_geojson = country_geometry.geometry().getInfo()
        folium.GeoJson(
            country_geojson,
            style_function=lambda x: {
                'fillColor': 'transparent',
                'color': 'red',
                'weight': 3,
                'fillOpacity': 0
            },
            popup=folium.Popup(f'{country_name} Boundary')
        ).add_to(m)
    except Exception as e:
        print(f"Could not add boundary: {e}")
    
    # Add colorbar
    colormap = folium.LinearColormap(
        colors=['#24126c', '#1fff4f', '#d4ff50'],
        vmin=0, vmax=50,
        caption=f'{band.title()} {year} (people per pixel)'
    )
    colormap.add_to(m)
    
    folium.LayerControl().add_to(m)
    
    return m

# Create initial map
current_map = create_country_year_map(
    country_dropdown.value,
    year_dropdown.value,
    population_band.value
)

current_map

🗺️ Creating map: Brazil, 2020, population
✅ Created mosaic for year 2020 from 243 images


## Update Map Function

In [8]:
def update_map(change=None):
    """Update map when parameters change"""
    new_map = create_country_year_map(
        country_dropdown.value,
        year_dropdown.value,
        population_band.value
    )
    display(new_map)
    return new_map

# Update button
update_button = widgets.Button(
    description='🔄 Update Map',
    button_style='success'
)

update_button.on_click(update_map)
display(update_button)

Button(button_style='success', description='🔄 Update Map', style=ButtonStyle())

## Compare Multiple Years

In [9]:
def compare_years(country_name, years_to_compare=[2010, 2015, 2020]):
    """Create a map comparing multiple years"""
    
    print(f"📊 Comparing years {years_to_compare} for {country_name}")
    
    # Get country info
    country = get_country_bounds(country_name)
    country_geometry = country.first()
    center_coords = get_country_center(country_geometry)
    
    # Create map
    m = folium.Map(location=center_coords, zoom_start=6)
    
    # Add each year as a separate layer
    colors = ['24126c', 'ff0000', '00ff00']  # Different colors for different years
    
    for i, year in enumerate(years_to_compare):
        try:
            worldpop_year = get_worldpop_for_year(year)
            pop_image = worldpop_year.select('population')
            
            vis_params = {
                'bands': ['population'],
                'min': 0.0,
                'max': 50.0,
                'palette': ['000000', colors[i % len(colors)]]
            }
            
            layer_name = f'Population {year}'
            m.add_ee_layer(pop_image, vis_params, layer_name)
            
        except Exception as e:
            print(f"Could not add year {year}: {e}")
    
    # Add country boundary
    country_geojson = country_geometry.geometry().getInfo()
    folium.GeoJson(
        country_geojson,
        style_function=lambda x: {'fillColor': 'transparent', 'color': 'yellow', 'weight': 2}
    ).add_to(m)
    
    folium.LayerControl().add_to(m)
    
    return m

# Create comparison map
comparison_map = compare_years(country_dropdown.value)
print("\n📈 Multi-year comparison map:")
comparison_map

📊 Comparing years [2010, 2015, 2020] for Brazil
✅ Created mosaic for year 2010 from 0 images
Could not add year 2010: Image.select: Band pattern 'population' was applied to an Image with no bands. See https://developers.google.com/earth-engine/guides/debugging#no-bands
✅ Created mosaic for year 2015 from 0 images
Could not add year 2015: Image.select: Band pattern 'population' was applied to an Image with no bands. See https://developers.google.com/earth-engine/guides/debugging#no-bands
✅ Created mosaic for year 2020 from 243 images

📈 Multi-year comparison map:
